# IBM Model 1 with Expectation Maximization

## Author: Anmol Sharma

**Open the files**

In [1]:
eng_set = open('../data/hansards.en', 'rb')
fr_set = open('../data/hansards.fr', 'rb')

**Perform Preprocessing**

1. **Split the data into two different sets, and split each sentence into words**
2. **Add a NONE character inside every english sentence**

In [2]:
src_sent = []
dest_sent = []

for line_en, line_fr in zip(eng_set, fr_set):
    # split each sentence into a list of words for easy processing
    src_sent.append(line_fr.split())
    dest_sent.append([None] + line_en.split())

We can see the words contain many "\xc3\xa9es"... which are basically the unicode codes for special accented symbols in french. Nothing to worry. 

Also, the punctuation marks are left as it is as "words" which map directly to the punctuation in the destination language. 

In [3]:
src_sent[5:10]

[['souvenons',
  '-',
  'nous',
  ',',
  'monsieur',
  'le',
  'Orateur',
  ',',
  'que',
  'ce',
  'sont',
  'ces',
  'secteurs',
  'de',
  'notre',
  'soci\xc3\xa9t\xc3\xa9',
  'qui',
  'servent',
  'de',
  '\xc3\xa9pine',
  'dorsale',
  '\xc3\xa0',
  'notre',
  '\xc3\xa9conomie',
  '.'],
 ['bravo', '!'],
 ['bravo', '!'],
 ['monsieur',
  'le',
  'Orateur',
  ',',
  'ma',
  'question',
  'se',
  'adresse',
  '\xc3\xa0',
  'le',
  'ministre',
  'charg\xc3\xa9',
  'de',
  'les',
  'transports',
  '.'],
 ['tous',
  'deux',
  'poss\xc3\xa8dent',
  'de',
  'nombreuses',
  'ann\xc3\xa9es',
  'de',
  'exp\xc3\xa9rience',
  'dans',
  'la',
  'fabrication',
  'et',
  'la',
  'distribution',
  'de',
  'les',
  'produits',
  'forestiers',
  '.']]

In [4]:
dest_sent[5:10]

[[None,
  'let',
  'us',
  'remember',
  ',',
  'Mr.',
  'Speaker',
  ',',
  'that',
  'these',
  'segments',
  'of',
  'our',
  'society',
  'form',
  'the',
  'backbone',
  'of',
  'our',
  'economy',
  '.'],
 [None, 'hear', ',', 'hear', '!'],
 [None, 'hear', ',', 'hear', '!'],
 [None,
  'Mr.',
  'Speaker',
  ',',
  'my',
  'question',
  'is',
  'directed',
  'to',
  'the',
  'Minister',
  'of',
  'Transport',
  '.'],
 [None,
  'both',
  'have',
  'many',
  'years',
  'experience',
  'in',
  'the',
  'manufacture',
  'and',
  'distribution',
  'of',
  'forest',
  'products',
  '.']]

## **We need to find the probability $t_k(f_i|e_j)$ where $f_i$ = french word (source language) and $e_j$ = english word (destination language)**

Find all the unique words in french data

In [5]:
import itertools

In [6]:
import numpy as np

In [7]:
# for i in itertools.chain.from_iterable(src_sent):
#     print(i)

In [8]:
# convert the source list into a chain of iterables, and then convert it to a set to only retain unique elements.
# further convert to list for easy processing
fr_vocab = list(set(itertools.chain.from_iterable(src_sent)))
en_vocab = list(set(itertools.chain.from_iterable(dest_sent)))

In [9]:
fr_vocab[0:5]

['1,800', 'engendr\xc3\xa9e', 'encouragerais', 'accueille', 'accueilli']

In [10]:
en_vocab[0:5]

['1,800', 'woods', 'hanging', 'trawling', 'originality']

## Initialize the conditional probability $t_k(f_i|e_j)$ with uniform probabilities

We need to initialize the probability for each of the word in french corresponding to each of the word in english. We will use a dictionary with keys of the form $(f_i, e_j)$ to represent $t_k(f_i|e_j)$.

Hence dict[$(f_i, e_j)$] = $t_k(f_i|e_j)$

In [ ]:
len(fr_vocab)

In [ ]:
len(en_vocab)

In [ ]:
t_k = {}
uni_prob = 1.0 / np.shape(fr_vocab)[0]

for _fr_wrd in fr_vocab:
    for _en_wrd in en_vocab:
        t_k[str(_fr_wrd) + '__' + str(_en_wrd)] = uni_prob

In [ ]:
t_k

For the given french sentence, we initialize an alignment dictionary which aligns the french sentence to each permutation of the english sentence. An efficient way is to use itertools. 

In [ ]:
alignments = []
for src_sent_eg, dest_sent_eg in zip(src_sent, dest_sent):
    for dest_permutation in itertools.permutations(dest_sent_eg):
        alignments.append([zip(src_sent_eg, dest_permutation)])

In [ ]:
alignments[0:5]

In [12]:
k = 0
t_k = {}
count_comb = {}
count_e = {}
uni_prob = 1.0 / np.shape(fr_vocab)[0]
epochs = 5

for _i in range(epochs):
    print('Currently on training epoch {}..'.format(_i+1))
    # iterate over all training examples
    for src_sent_eg, dest_sent_eg in zip(src_sent, dest_sent):
        for f_i in src_sent_eg:
            Z = 0.0
            for e_j in dest_sent_eg:
                
                if (f_i, e_j) not in t_k:
#                     print('({}, {}) not in t_k, initializing to uniform!'.format(f_i, e_j))
                    t_k[(f_i, e_j)] = 1.0 / uni_prob
                
                Z += t_k[(f_i, e_j)]
            for e_j in dest_sent_eg:
                c = t_k[(f_i, e_j)] / Z
                
                # initialize counts on the fly
                if (f_i, e_j) not in count_comb:
#                     print('({}, {}) not in count_comb, initializing to 0!'.format(f_i, e_j))
                    count_comb[(f_i, e_j)] = 0
                
                # initialize counts on the fly
                if e_j not in count_e:
#                     print('({}) not in count_e, initializing to 0!'.format(e_j))
                    count_e[e_j] = 0
                    
                count_comb[(f_i, e_j)] += c
                count_e[e_j] += c
    print('Updating t_k counts...')
    for f_e_keys in count_comb:
        # f_e_keys[0] = f_i, f_e_keys[1] = e_j
        t_k[(f_e_keys[0], f_e_keys[1])] = count_comb[f_e_keys] / count_e[f_e_keys[1]]

Currently on training epoch 1..
Updating t_k counts...


# Make predictions using this trained model..

In [16]:
print('Aligning...')
print('Source | Destination')
for src_sent_eg, dest_sent_eg in zip(src_sent, dest_sent):
    for f_i in src_sent_eg:
        bestp = 0
        bestj = 0
        
        for e_j in dest_sent_eg:
            if t_k[(f_i, e_j)] > bestp:
                bestp = t_k[(f_i, e_j)]
                bestj = e_j
        print('{} | {}'.format(f_i, bestj))

Aligning...
Source | Destination
2 | 2
. | .
2 | 2
. | .
oh | oh
, | oh
oh | oh
! | oh
oh | oh
, | oh
oh | oh
! | oh
oh | oh
, | oh
oh | oh
! | oh
souvenons | segments
- | Mr.
nous | us
, | ,
monsieur | Speaker
le | Speaker
Orateur | segments
, | ,
que | that
ce | backbone
sont | backbone
ces | these
secteurs | segments
de | backbone
notre | our
société | society
qui | segments
servent | segments
de | backbone
épine | segments
dorsale | segments
à | segments
notre | our
économie | economy
. | Mr.
bravo | hear
! | !
bravo | hear
! | !
monsieur | Speaker
le | Speaker
Orateur | directed
, | ,
ma | my
question | question
se | question
adresse | question
à | directed
le | Speaker
ministre | Minister
chargé | directed
de | of
les | Transport
transports | Transport
. | Mr.
tous | forest
deux | both
possèdent | forest
de | manufacture
nombreuses | forest
années | years
de | manufacture
expérience | experience
dans | forest
la | forest
fabrication | manufacture
et | forest
la | forest
distribut

cette | suggestion
suggestion | suggestion
. | Mr.
1 | 98,355
. | 98,355
a | 98,355
) | 98,355
$ | 98,355
98,355 | 98,355
. | 98,355
b | 98,355
) | 98,355
Ils | 98,355
sont | 98,355
disponibles | 98,355
dans | 98,355
tous | 98,355
les | offices
grands | 98,355
bureaux | 98,355
de | $
poste | 98,355
de | $
le | post
pays | 98,355
. | 98,355
en | while
vertu | constitution
de | enforcement
la | constitution
constitution | constitution
, | ,
le | problem
activité | constitution
criminelle | enforcement
est | is
de | enforcement
compétence | provincial
fédérale | provincial
, | ,
tandis | while
que | while
le | problem
application | enforcement
de | enforcement
la | constitution
loi | law
relève | responsibility
de | enforcement
les | local
provinces | provincial
et | and
de | enforcement
les | local
municipalités | constitution
. | .
je | i
prétends | submit
que | what
mes | pertinent
remarques | pertinent
concernant | pertinent
le | medicare
bill | pertinent
, | ,
le | medicare
argent | 

détaillés | industrial
que | should
il | should
faut | should
mettre | set
à | to
le | plan
point | developed
. | .
on | construct
dit | construct
maintenant | now
que | we
la | construct
construction | construct
de | construct
le | the
gazoduc | construct
va | construct
coûter | construct
environ | construct
45 | 45
milliards | billion
de | construct
dollars | billion
. | .
signalons | flaws
par | reflected
ailleurs | flaws
que | are
on | are
trouve | flaws
toutes | flaws
ces | these
lacunes | flaws
dans | reflected
le | bill
bill | flaws
. | .
a | there
ce | this
stade | stage
de | proposes
le | stage
débat | debate
sur | debate
la | resolution
résolution | resolution
, | ,
mon | my
parti | party
propose | proposes
trois | three
amendements | amendments
précis | specific
. | .
il | there
ne | cannot
peut | cannot
donc | means
pas | cannot
prétendre | claim
avoir | claim
apporté | change
le | government
moindre | any
changement | change
à | in
le | government
niveau | ways
de | ways
l

cause | alerting
de | alerting
ce | alerting
qui | alerting
se | alerting
est | alerting
passé | alerting
. | .
Évidemment | course
, | ,
quand | they
les | Conservatives
conservateurs | Conservatives
étaient | Conservatives
dans | in
le | Opposition
opposition | Opposition
, | ,
ils | they
tenaient | contrary
de | of
les | Conservatives
discours | said
qui | what
étaient | Conservatives
à | contrary
le | Opposition
opposé | Conservatives
de | of
leurs | they
actions | contrary
de | of
aujourd' | now
hui | now
. | Opposition
en | fact
réalité | beings
, | ,
le | Solicitor
ministre | Minister
de | of
la | Justice
Justice | Justice
et | and
le | Solicitor
solliciteur | Solicitor
général | Solicitor
ont | responded
répondu | responded
avec | responded
tous | beings
les | human
détails | beings
que | beings
ils | beings
pouvaient | beings
humainement | beings
donner | beings
. | Solicitor
le | Deputy
vice | Deputy
- | Deputy
premier | Prime
ministre | Prime
croit | believe
- | Deputy
il | 

les | additional
budgets | additional
supplémentaires | additional
. | .
bon | well
, | ,
tout | everyone
le | everyone
monde | everyone
est | that
de | with
accord | agree
là | agree
- | ,
dessus | agree
. | .
le | chief
poste | executive
de | executive
directeur | executive
général | executive
a | there
été | was
vacant | permanent
durant | permanent
plus | over
de | executive
un | officer
an | 12
, | 12
et | executive
pour | for
cause | permanent
. | .
le | Minister
ministre | Minister
a | spoke
parlé | spoke
de | meetings
réunions | meetings
, | I
fort | applaud
bien | applaud
. | .
il | 's
fallait | 's
que | 's
il | 's
soit | 's
à | to
Saint | 's
- | St.
Jean | 's
. | John
ce | happening
est | is
exactement | description
ce | happening
qui | happening
se | happening
passe | happening
. | .
il | be
ne | cannot
est | .
pas | cannot
question | isolation
de | isolation
les | isolation
traiter | isolation
séparément | isolation
. | .
de | eastern
toute | obviously
évidence | obviously


...

. | .
elle | was
a | was
revêtu | huge
beaucoup | huge
de | huge
importance | issue
à | in
le | the
cours | campaign
de | huge
la | campaign
campagne | campaign
électorale | campaign
. | .
la | majority
majorité | majority
de | s
le | government
gouvernement | government
a | diminished
diminué | diminished
. | .
que | what
est | ?
- | ?
ce | what
que | what
cela | does
signifie | does
en | programs
ce | what
qui | what
concerne | has
le | the
appui | support
de | programs
la | the
population | programs
pour | for
ses | its
programmes | programs
? | ?
il | barest
a | barest
la | barest
plus | barest
faible | barest
de | majorities
les | majorities
majorités | barest
à | barest
le | barest
heure | barest
actuelle | barest
. | barest
nombreuses | many
provinces | provinces
, | ,
comme | as
le | Alberta
Alberta | Alberta
, | ,
ont | consulted
consulté | consulted
leurs | their
citoyens | citizens
directement | directly
à | instead
le | Alberta
lieu | instead
de | many
simplement | simply
t

le | government
atteinte | surpassed
de | targets
les | demands
objectifs | objectives
et | underemployment
de | targets
le | government
dépassement | surpassed
de | targets
les | demands
cibles | surpassed
déficitaires | surpassed
, | surpassed
que | that
le | government
gouvernement | government
fédéral | federal
devrait | should
répondre | surpassed
à | met
nos | our
demandes | demands
se | if
il | wants
a | deficit
vraiment | really
en | underemployment
tête | surpassed
de | targets
lutter | surpassed
contre | surpassed
la | poverty
pauvreté | poverty
, | surpassed
lutter | surpassed
contre | surpassed
le | government
sous | underemployment
- | underemployment
emploi | underemployment
. | .
il | it
devrait | should
remettre | stolen
ce | what
que | what
il | it
a | has
volé | stolen
à | back
les | provinces
provinces | provinces
, | stolen
ce | what
est | what
pas | should
mêlant | stolen
. | .
il | it
devrait | should
cesser | stop
, | ,
dès | immediately
cette | stop
année | budg

Que | Appelle
Appelle | Appelle
, | ,
NPD | NDP
) | )
: | :
je | i
veux | want
de | electing
abord | first
remercier | thank
les | voters
électeurs | voters
de | electing
Que | Appelle
Appelle | Appelle
de | electing
me | me
avoir | electing
élu | electing
député | member
. | Appelle
je | Wynyard
ai | Wynyard
représenté | Wynyard
la | Wynyard
circonscription | Wynyard
de | Commons
Yorkton | Yorkton
- | Melville
Melville | Melville
durant | Wynyard
25 | 25
ans | Wynyard
, | hometown
mais | Wynyard
ce | Wynyard
est | is
la | Wynyard
première | Wynyard
fois | Wynyard
que | that
je | Wynyard
ai | Wynyard
la | Wynyard
chance | Wynyard
de | Commons
représenter | Wynyard
ma | Wynyard
ville | hometown
natale | Wynyard
, | hometown
Wynyard | Wynyard
, | hometown
à | House
la | Wynyard
Chambre | Commons
de | Commons
les | Commons
communes | Commons
. | Melville
je | i
en | really
suis | am
très | pleased
heureux | pleased
. | .
je | i
veux | want
aussi | also
prendre | take
un | a
petit | predec

offrant | alternative
une | an
possibilité | choice
de | billion
choix | choice
à | border
ces | those
Canadiens | care
qui | who
dépensent | money
déjà | already
2 | 2
milliards | billion
de | billion
dollars | billion
outre | border
- | ?
frontière | border
? | ?
que | that
on | spend
laisse | medical
les | care
gens | people
dépenser | spend
ici | here
de | care
sorte | so
que | that
de | care
nouveaux | new
emplois | jobs
puissent | so
se | care
créer | jobs
dans | in
le | the
secteur | created
de | care
les | care
soins | care
médicaux | medical
. | let
si | if
le | member
député | member
voulait | Sweden
bien | Sweden
considérer | Sweden
les | services
exemples | examples
de | plans
autres | other
pays | countries
qui | which
ont | have
pris | Zealand
de | plans
les | services
mesures | Zealand
en | Britain
ce | this
sens | Sweden
, | ,
comme | as
la | Sweden
Grande | Britain
- | Britain
Bretagne | Britain
, | ,
la | Sweden
Suède | Sweden
et | Sweden
la | Sweden
Nouvelle | Zealan

KeyboardInterrupt: 